# IMPES for homogeneous quarter-five spot (Mixed FEM + RKDG)

##### Pressure equation:

$$
\left\{
\begin{aligned}
\nabla \cdot u &= 0\\
\lambda_t^{-1} K^{-1} u+\nabla p &= 0
\end{aligned}
\right.
$$
##### Saturation equation:
$$
\phi\frac{\partial S_w}{\partial t} + \nabla \cdot (f_wu) = 0
$$

Corey model for relative mobilies (viscosity $\mu=1$):
$$
\lambda_t = S_w^2/\mu_w+(1-S_w)^2/\mu_o, \quad f_w = \frac{S_w^2/\mu_w}{S_w^2/\mu_w+(1-S_w)^2/\mu_o}
$$

##### Domain, source/sink, boundary conditions:
Boundary condition for saturation: $S_w=1$ at injector.
<img src="quarter.png" alt="Drawing" style="width: 400px;"/>

##### Source/sink implementation:
Here we introduce another common treatment for point source/sink.
Assume the source/sink is a Dirac delta function with strength $+1/4$, $-1/4$ respectively.

We calculate an equivalent distribution of normal velocity $g$ on the domain boundary
and drive the problem with $g$, setting $q=0$. Here 
$$
g = \left\{
\begin{aligned}
-\frac{1}{8h}&\quad \text{ near bottom left corner}\\[.3ex]
\frac{1}{8h}&\quad \text{ near top right corner}\\[.3ex]
\\
0&\quad\text{ else where}
\end{aligned}
%\begin{tabular}{ll}
%$\frac{-1}{8h}$& near bottom left corner\\[.3ex]
%0& else\\
%\end{tabular}
\right.
$$

+ This boundary condition also satisfy the compatibity condition:
$$
0 = \int_{\partial\Omega}u\cdot n\,\mathrm{ds} = \int_{\Omega}\nabla\cdot u\,\mathrm{dx}
 = 0.
$$

##### Nondimentionalization
We consider a nondimensional domain with unit length $\Omega = [0,1]\times [0,1]$.
Homogeneous material parameters:
$$
\mu_w=\mu_n = 1, K=1, \phi= 1.
$$

In [1]:
from ngsolve import *
from ngsolve.webgui import Draw # webgui
from netgen.geom2d import SplineGeometry
import numpy as np
import sys # 

# a mesh for unit square domain with specific boundary flags at corners
def quarterFiveSpot(h0):
    geometry = SplineGeometry()
    
    # point coordinates ...
    pnts = [ (0,0), (h0,0), (1,0), (1,1-h0), \
            (1,1), (1-h0,1), (0,1), (0,h0)]
    pnums = [geometry.AppendPoint(*p) for p in pnts]   
    
    # start-point, end-point, boundary-condition, domain on left side, domain on right side:
    lines = [ (0,1,"bottomLeft",1,0), (1,2,"free",1,0), (2,3,"free",1,0), (3,4,"topRight",1,0),
             (4,5,"topRight",1,0), (5,6,"free",1,0),
             (6,7,"free",1,0), (7,0,"bottomLeft",1,0)]
    for p1,p2,bc,left,right in lines:
        geometry.Append( ["line", pnums[p1], pnums[p2]], bc=bc, leftdomain=left, rightdomain=right)
    return geometry

### generate mesh using quarterFiveSpot geometry
h0 = 0.025
geo = quarterFiveSpot(h0)
mesh = Mesh(geo.GenerateMesh(maxh=h0))
Draw(mesh)

mesh.GetBoundaries()

NGSWebGuiWidget(value={'ngsolve_version': '6.2.2006', 'mesh_dim': 2, 'order2d': 1, 'order3d': 1, 'draw_vol': N…

('bottomLeft',
 'free',
 'free',
 'topRight',
 'topRight',
 'free',
 'free',
 'bottomLeft')

### parameters/functions

In [8]:
# porosity, inverse permeability
phi, invK = 1, 1
# viscosities
muw, muo = 1, 1

## functions of saturation
def invLamT(s): # inverse lambda T
    # scale s to be in range [0,1]
    s = IfPos(s-1, 1-s, 0)+IfPos(s, 0, -s) + s
    lamT = s**2/muw+(1-s)**2/muo
    return 1/lamT

def fw(s):
    # scale s to be in range [0,1]
    s = IfPos(s-1, 1-s, 0)+IfPos(s, 0, -s) + s
    lamW = s**2/muw
    lamT = lamW + (1-s)**2/muo
    return lamW/lamT

import time as timeit

## Putting it together, allow higher-order FEMs, and add subcycling: 
+ compile coefficient functions: see this [link](https://ngsolve.org/docu/latest/i-tutorials/unit-1.2-coefficient/coefficientfunction.html)

In [21]:
# the IMPES solver
def IMPESSolver(mesh=mesh, kmx=0, kdg=0, rk3=False, cfl = 0.3, tend = 3, nStepsP = 60, nplot = 30, vis=True
               , true_compile=False):
    # kmx: pressure solve poly degree
    # kdg: saturation solve poly degree
    ### FESpaces (pressure) kmx=0: RT0-P0, kmd>0: BDMk-P(k-1)
    V = HDiv(mesh, order=kmx, discontinuous=True)
    W = L2(mesh, order=kmx-1+(kmx==0))
    M = FacetFESpace(mesh, order=kmx) # facet fespace, hybrid unknown for pressure on skeleton
    fesP = FESpace([V,W, M])
    # fix pressure null space
    fesP.FreeDofs()[V.ndof+W.ndof] = False 
    fesP.FreeDofs(True)[V.ndof+W.ndof] = False 
    gfuP = GridFunction(fesP)
    uh, ph, phath = gfuP.components 

    ### FESpaces (saturation): DG-P0
    fesS = L2(mesh, order=kdg)
    gfuS = GridFunction(fesS)
    
    # inverse lambda_t: function of saturation
    invLamTS = invLamT(gfuS)

    ###### pressure bilinear/linear forms
    (u,p, phat), (v,q, qhat) = fesP.TnT()  # symbolic object, test and trial ProxyFunctions
    n = specialcf.normal(mesh.dim)  

    a = BilinearForm(fesP, condense=True, symmetric=True)
    a += (invLamTS*invK*u*v-p*div(v)-q*div(u))*dx
    # the hybridization
    a += (phat*v*n+qhat*u*n)*dx(element_boundary=True)

    f = LinearForm(fesP) # boundary source term strength 0.125/h0
    f += -0.125/h0*qhat.Trace()*ds("bottomLeft") # boundary integral
    f += 0.125/h0*qhat.Trace()*ds("topRight") # boundary integral

    f.Assemble() # f does not dependent on time, pre-assemble it

    ##### saturation bilinear/linear forms
    ####### FIXME: this default version is very slow, even with compiling
    ####### FIXME: this default version is very slow, even with compiling
    ####### FIXME: this default version is very slow, even with compiling
    ss, tt = fesS.TnT()  # symbolic object, test and trial ProxyFunctions

    aS = BilinearForm(fesS, nonassemble=True) # do not assemble matrix
    # volume integration (it is not needed for DG-P0)
    if kdg>0:
        aS += -uh*fw(ss).Compile(true_compile, wait=True)*grad(tt)*dx
    # element-boundary integration
    Fhat = IfPos(uh*n, fw(ss), fw(ss.Other(bnd=1))) # incoporate saturation boundary condition at inflow  
    ## FIXME: if you didn't compile 
    aS += uh*n*Fhat*tt.Compile(true_compile, wait=True)*dx(element_boundary=True) ##### element_boundary formuation

    # inverse of diagonal mass matrix (phi ss, tt) (only work for L2 FE space)
    invm = fesS.Mass(phi).Inverse() # pay attention to phi !!!!

    rhsP = gfuP.vec.CreateVector()
    rhsS = gfuS.vec.CreateVector()
    s1 = gfuS.vec.CreateVector()
    s2 = gfuS.vec.CreateVector()

    # forward euler time stepping
    def ForwardEuler(sh, dt): # sh is a base vector
        # forward euler step
        # s^{j} --> s^{j+1}
        rhsS.data = aS.mat * sh
        rhsS.data = invm*rhsS
        return sh-dt*rhsS
    
    # time stepping
    time = 0.
    tplot = tend/nplot
    
    stepP, stepS = 0, 0 # pressure and saturation steps
    timeP, timeS = 0, 0 # pressure and saturation step timing

    ### pre-determinte time step size based on estimated velocity magnitude 
    ########## apply pressure solve to estimate maximum velocity magnitude
    a.Assemble()
    rhsP.data = f.vec 
    rhsP.data += a.harmonic_extension_trans * rhsP
    gfuP.vec.data = a.mat.Inverse(fesP.FreeDofs(True),inverse="umfpack") * rhsP
    gfuP.vec.data += a.harmonic_extension * gfuP.vec
    gfuP.vec.data += a.inner_solve * rhsP
    ########## end apply pressure solve to estimate maximum velocity magnitude

    # project velocity norm to P0 space then estimate the maximum velocity mag.
    vel0 = GridFunction(L2(mesh)) 
    vel0.Set(uh**2) 
    velmax = max(vel0.vec)**0.5 
    dt = phi*cfl*h0/velmax #### time step size
    print('velmax: %.2f   dt: %.2e,  nsteps: %4d'%(velmax, dt, int(tend/dt)))

    # subcycle pressure steps
    nsteps = int((tend+dt/2)/dt)     # total # steps
    nsubcycles = int(nsteps/nStepsP) # only update pressure ~ nStepsP times    

    #### initialization: set-zero saturation
    gfuS.vec[:] = 0 # initial saturation is zero
    if vis:
        scene = Draw(gfuS, mesh, "saturation", min=0, max = 1, autoscale=False)
    gfuSt = GridFunction(fesS, multidim=0) # store time history of data for later visualization

    with TaskManager():
        while  time < tend-dt/2 :
            t0 = timeit.time() # timer
            if stepS%nsubcycles == 0:
                # implicit pressure to update velocity
                a.Assemble()
                rhsP.data = f.vec # source term
                rhsP.data += a.harmonic_extension_trans * rhsP
                gfuP.vec.data = a.mat.Inverse(fesP.FreeDofs(True),inverse="sparsecholesky") * rhsP
                gfuP.vec.data += a.harmonic_extension * gfuP.vec
                gfuP.vec.data += a.inner_solve * rhsP
                stepP += 1
            t1 = timeit.time() # timer
            timeP += t1-t0

            # explicit saturation (FE or RK3)
            if rk3:
                s1.data = ForwardEuler(gfuS.vec, dt)
                s2.data = 0.75*gfuS.vec+0.25*ForwardEuler(s1, dt)
                gfuS.vec.data = 1/3*gfuS.vec+2/3*ForwardEuler(s2, dt) 
            else: 
                gfuS.vec.data = ForwardEuler(gfuS.vec, dt)

            t2 = timeit.time() # timer            
            stepS += 1
            timeS += t2-t1

            # update time
            time += dt
            if time > tplot-dt/2:
                t1 = timeit.time() # timer
                tplot += tend/nplot
                if vis:
                    scene.Redraw()
                gfuSt.AddMultiDimComponent(gfuS.vec)
                ### output progress bar
                progress = int((time+dt)/tend*100)
                sys.stdout.write('\r')
                # the exact output you're looking for:
                sys.stdout.write("[%-20s] %d%%  pres step: %4d cost:%.2f, satu step: %5d cost:%.2f"
                                 %('='*int(progress/5), progress, stepP, timeP, stepS, timeS))
                sys.stdout.flush()
    print('\n\n') 
    return gfuSt

### We use the same finite elements: RT0 for pressure, DGP0 for saturation, but enable subcycling
+ With subcycling saturation, pressure is solved only 60 times, which saturation is solved about 2800 times (roughly update pressure every 40 saturation updates)
+ Explicit saturation solver now became the bottleneck. We need to do something to speed it up.

In [18]:
%%time
# now saturation solver becomes the bottleneck
gfuSt0 = IMPESSolver(vis=False)

velmax: 7.15   dt: 1.05e-03,  nsteps: 2858
[====================] 100%  pres step:   61 cost:0.98, satu step:  2858 cost:9.57


CPU times: user 2min 39s, sys: 4.39 s, total: 2min 44s
Wall time: 10.7 s


In [19]:
%%time
# now saturation solver becomes the bottleneck
gfuSt0 = IMPESSolver(true_compile=True, vis=False)

velmax: 7.15   dt: 1.05e-03,  nsteps: 2858
[====================] 100%  pres step:   61 cost:1.00, satu step:  2858 cost:9.99


CPU times: user 2min 47s, sys: 4.09 s, total: 2min 51s
Wall time: 13.3 s


In [16]:
# of course, we can also animate the saturation evolution
Draw (gfuSt0, mesh, interpolate_multidim=True, animate=True, min=0, max=1, autoscale=False)

NGSWebGuiWidget(value={'ngsolve_version': '6.2.2006', 'mesh_dim': 2, 'order2d': 2, 'order3d': 1, 'draw_vol': F…